In [1]:
import napari
import os
from tqdm import tqdm
import numpy as np
import glob2 as glob
import zarr
import json
import skimage.io as io
import pandas as pd
import umap.umap_ as umap
from sklearn.preprocessing import StandardScaler

# # set parameters
root = "/Users/nick/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/killi_tracker/"
project_name = "240219_LCP1_93hpf_to_127hpf"
image_dir = os.path.join(root, "built_data", project_name, "")
config_name = "tracking_cell.txt" 
tracking_folder = config_name.replace(".txt", "")
tracking_folder = tracking_folder.replace(".toml", "")

tracking_directory = os.path.join(root, "built_data", "tracking", project_name, tracking_folder)
snip_directory = os.path.join(root, "built_data", "shape_snips", project_name, tracking_folder, "class0")

# load metadata
metadata_file_path = os.path.join(root, "metadata", project_name, "metadata.json")
f = open(metadata_file_path)
metadata = json.load(f)
scale_vec = np.asarray([metadata["ProbPhysicalSizeZ"], metadata["ProbPhysicalSizeY"], metadata["ProbPhysicalSizeX"]])

In [2]:
# load track
tracks_df = pd.read_csv(os.path.join(tracking_directory, "tracks.csv"))
tracks_df["z"] = tracks_df["z"] * scale_vec[0]
tracks_df["y"] = tracks_df["y"] * scale_vec[1]
tracks_df["x"] = tracks_df["x"] * scale_vec[2]
tracks_df.head()

track_id  t    z      y      x       id  parent_track_id  parent_id
0         1  0  6.0  351.0  171.0  1000001               -1         -1
1         1  1  6.0  354.0  168.0  2000001               -1    1000001
2         1  2  6.0  357.0  165.0  3000001               -1    2000001
3         1  3  6.0  357.0  165.0  4000001               -1    3000001
4         1  4  6.0  360.0  171.0  5000001               -1    4000001

In [3]:
shape_df = pd.read_csv(os.path.join(tracking_directory, "cell_shape_df_refined.csv"))
shape_df.head()

track_id  t  coeff_row00_col0  coeff_row00_col1  coeff_row00_col2  \
0         1  0          5.682911          1.873089          5.580247   
1         1  1          5.203696          2.614778          7.537178   
2         1  2          5.644366          1.613402          5.684188   
3         1  3          5.406232          2.111145          8.253573   
4         1  4          5.702678          1.870952          5.000900   

   coeff_row00_col3  coeff_row01_col0  coeff_row01_col1  coeff_row01_col2  \
0         -7.141475          0.940136          0.858053         -0.916367   
1         -6.216010          0.729461          1.207593         -0.749521   
2         -5.990444          0.943012          1.110027         -0.892641   
3         -5.076999          1.160169          0.987926         -1.064323   
4         -6.541060          0.650244          1.084818         -0.529999   

   coeff_row01_col3  ...  coeff_row09_col1  coeff_row09_col2  \
0         -0.389856  ...         -0.067701          0.043263   
1         -0.466452  ...          0.110919          0.023741   
2         -0.858211  ...          0.004049          0.056090   
3         -1.670919  ...          0.054617          0.173997   
4         -0.305031  ...          0.037492         -0.031438   

   coeff_row09_col3  perimeter  complexity   area  solidity  eccentricity  \
0          0.046716  53.420310    1.187650  161.0  0.904494      1.668613   
1         -0.023134  55.970563    1.236690  163.0  0.867021      1.918781   
2         -0.000654  49.763456    1.194995  138.0  0.836364      1.608210   
3         -0.007699  64.384776    1.440389  159.0  0.807107      2.132538   
4         -0.075528  50.384776    1.172292  147.0  0.896341      1.593195   

   lcp_intensity  circularity  
0      18.218081     0.550208  
1      18.326858     0.472179  
2      20.072262     0.551903  
3      20.032844     0.394468  
4      20.961073     0.575682  

[5 rows x 49 columns]

In [4]:
shape_df.loc[(shape_df["track_id"]==29) & (shape_df["t"]==90)]

track_id   t  coeff_row00_col0  coeff_row00_col1  coeff_row00_col2  \
2437        29  90          6.676721          -0.79814          -4.99639   

      coeff_row00_col3  coeff_row01_col0  coeff_row01_col1  coeff_row01_col2  \
2437         -7.076856          -0.81134         -0.149929         -0.463165   

      coeff_row01_col3  ...  coeff_row09_col1  coeff_row09_col2  \
2437         -0.597562  ...         -0.008466         -0.063848   

      coeff_row09_col3  perimeter  complexity   area  solidity  eccentricity  \
2437          0.017175  56.627417    1.228792  169.0  0.840796      2.130439   

      lcp_intensity  circularity  
2437      41.465319     0.418337  

[1 rows x 49 columns]

In [ ]:
master_df = tracks_df.merge(shape_df, on=["track_id", "t"], how="left")

In [ ]:
from tqdm import tqdm
dt = 90

window_size_vec = [1, 5, 11, 25]

for window_size in window_size_vec:
    w_str = str(window_size)
    c_time = dt*window_size
    buffer_size = window_size // 2
    track_index = np.unique(master_df["track_id"])

    for t, track_id in enumerate(tqdm(track_index)):
        track_bool = (master_df["track_id"] == track_id).to_numpy()

        if np.sum(track_bool) >= window_size:
            xyz = tracks_df.loc[track_bool, ["x", "y", "z"]].to_numpy()

            # get contour length
            d1 = np.sqrt(np.sum(np.diff(xyz, 1, axis=0)**2, axis=1))
            d1_cs = np.cumsum(d1)
            cs1 = d1_cs[window_size-1:]
            cs2 = np.concatenate(([0], d1_cs[:-window_size]))
            contour_r = cs1 - cs2

            # get net displacement
            net_r = np.sqrt(np.sum((xyz[window_size:, :] - xyz[:-window_size, :])**2, axis=1))

            # assign to tracks df
            to_indices = np.where(track_bool)[0]
            to_indices = to_indices[buffer_size:-buffer_size-1]
            master_df.loc[to_indices, "speed_" + w_str] = contour_r / c_time
            master_df.loc[to_indices, "speed_net_" + w_str] = net_r / c_time
            master_df.loc[to_indices, "coherence_" + w_str] = net_r / contour_r


        

In [ ]:
shape_metric_cols = ["complexity", "area", "solidity", "eccentricity", "lcp_intensity", "circularity", "perimeter"]

for window_size in window_size_vec:
    for col in shape_metric_cols:
        for t, track_id in enumerate(track_index):
            track_bool = (master_df["track_id"] == track_id).to_numpy()
            master_df.loc[track_bool, col + "_" + str(window_size)] = \
            master_df.loc[track_bool, col].rolling(window_size, center=True, min_periods=1).mean() #/ scale_vec[0]


In [ ]:
import plotly.express as px

track_id = 4
fig = px.scatter(master_df.loc[master_df["track_id"]==track_id], x="t", y="speed_5", color="t", template="plotly")
fig.show()

In [ ]:
fig = px.density_contour(master_df, x="lcp_intensity_5", y="speed_5")
fig.update_traces(contours_coloring="fill", contours_showlabels = True, colorscale="Blues")
fig.show()

In [ ]:
fig = px.density_contour(master_df, x="perimeter_11", y="coherence_11")
fig.update_traces(contours_coloring="fill", contours_showlabels = True, colorscale="Blues")
fig.show()

## Calculate "per-cell" statistics

In [12]:
track_index = np.unique(master_df["track_id"])
keep_cols = []

cell_stats_df = master_df.groupby(["track_id"]).mean().iloc[:, ]

# min_frames = 20
# dt = 90

# for t, track_id in enumerate(track_index):
#     track_bool = (master_df["track_id"] == track_id).to_numpy()
#     to_bool = (cell_stats_df["track_id"] == track_id).to_numpy()

#         if np.sum(track_bool) >= min_frames:
#             xyz = tracks_df.loc[track_bool, ["x", "y", "z"]].to_numpy()

#             # get contour length
#             v = np.sqrt(np.sum(np.diff(xyz, 1, axis=0)**2, axis=1)) / dt
            
            
#             d1_cs = np.cumsum(d1)
#             cs1 = d1_cs[window_size-1:]
#             cs2 = np.concatenate(([0], d1_cs[:-window_size]))
#             contour_r = cs1 - cs2

#             # get net displacement
#             net_r = np.sqrt(np.sum((xyz[window_size:, :] - xyz[:-window_size, :])**2, axis=1))

#             # assign to tracks df
#             to_indices = np.where(track_bool)[0]
#             to_indices = to_indices[buffer_size:-buffer_size-1]
#             master_df.loc[to_indices, "speed_" + w_str] = contour_r / c_time
#             master_df.loc[to_indices, "speed_net_" + w_str] = net_r / c_time
#             master_df.loc[to_indices, "coherence_" + w_str] = net_r / contour_r



In [ ]:
fig = px.scatter(cell_stats_df, x="speed_5", y="perimeter_5")
fig.show()

In [ ]:
n_components = 3

coeff_cols = [c for c in master_df.columns if "coeff" in c]

shape_array = master_df.loc[:, coeff_cols].to_numpy()

reducer = umap.UMAP(n_components=n_components)
# scaled_shape_array = StandardScaler().fit_transform(shape_array)
shape_embedding = reducer.fit_transform(shape_array)

master_df["UMAP00"] = shape_embedding[:, 0]
master_df["UMAP01"] = shape_embedding[:, 1]
master_df["UMAP02"] = shape_embedding[:, 2]

In [ ]:
import plotly.express as px
fig = px.scatter_3d(master_df, x="UMAP00", y="UMAP01", z="UMAP02", opacity=0.2)
fig.show()

In [13]:
from sklearn.decomposition import PCA

pca = PCA(n_components=5)
pca.fit(shape_array)
shape_pca_array = pca.transform(shape_array)
print(pca.explained_variance_ratio_)

[0.57762791 0.19924142 0.10089155 0.04939088 0.01292325]


In [24]:
master_df["shape_pca0"] = shape_pca_array[:, 0]
master_df["shape_pca1"] = shape_pca_array[:, 1]
master_df["shape_pca2"] = shape_pca_array[:, 2]

fig = px.scatter_3d(master_df, x="shape_pca0", y="shape_pca1", z="shape_pca2", color="eccentricity", opacity=0.2)
fig.show()

In [19]:
fig = px.density_contour(master_df, x="shape_pca2", y="speed_5")
fig.update_traces(contours_coloring="fill", contours_showlabels = True, colorscale="Blues")
fig.show()

In [20]:
import pyefd
n_components = 10
test = pyefd.reconstruct_contour(np.reshape(shape_array[(shape_df["track_id"]==287) & (shape_df["t"]==966)
                                                        , :(n_components*4)], (n_components, 4)))
fig = px.scatter(x=test[:, 0], y=test[:, 1])
fig.show()

In [23]:
master_df.loc[(shape_df["track_id"]==287) & (shape_df["t"]==966), 
                          ["shape_pca0", "shape_pca1", "shape_pca2"]]

shape_pca0  shape_pca1  shape_pca2
16593   12.983017    4.241964     0.12709